# Capstone Project - The Battle of the Neighborhoods (Week 2)
### Applied Data Science Capstone by IBM/Coursera

## Table of contents
* [Introduction: Business Problem](#introduction)
* [Data](#data)
* [Methodology](#methodology)
* [Analysis](#analysis)
* [Results and Discussion](#results)
* [Conclusion](#conclusion)



## Introduction: Business Problem <a name="introduction"></a>

In this project we will try to find an optimal location for a restaurant. Specifically, this report will be targeted to stakeholders interested in opening an **Italian restaurant** in **Paris**, France.

Since there are lots of restaurants in Paris we will try to detect **locations that are not already crowded with restaurants**. We are also particularly interested in **areas with no Italian restaurants in vicinity**. We would also prefer locations **as close to city center as possible**, assuming that first two conditions are met.

We will use our data science powers to generate a few most promissing neighborhoods based on this criteria. Advantages of each area will then be clearly expressed so that best possible final location can be chosen by stakeholders.

## Data <a name="data"></a>

Based on definition of our problem, factors that will influence our decission are:
* number of existing restaurants in the neighborhood (any type of restaurant)
* number of and distance to Italian restaurants in the neighborhood, if any
* distance of neighborhood from city center

We decided to use regularly spaced grid of locations, centered around city center, to define our neighborhoods.

Following data sources will be needed to extract/generate the required information:
* centers of candidate areas will be generated algorithmically and approximate addresses of centers of those areas will be obtained using **Google Maps API reverse geocoding**
* number of restaurants and their type and location in every neighborhood will be obtained using **Foursquare API**
* coordinate of Paris center will be obtained using **Google Maps API geocoding** of well known Paris location (Place de la République)

### Neighborhood Candidates

Let's create latitude & longitude coordinates for centroids of our candidate neighborhoods. We will create a grid of cells covering our area of interest which is aprox. 12x12 killometers centered around Paris city center.

Let's first find the latitude & longitude of Paris city center, using specific, well known address and Google Maps geocoding API.

In [15]:
google_api_key = 'Getityouself'

In [71]:
import requests

def get_coordinates(api_key, address, verbose=False):
    try:
        url = 'https://maps.googleapis.com/maps/api/geocode/json?key={}&address={}'.format(api_key, address)
        response = requests.get(url).json()
        if verbose:
            print('Google Maps API JSON result =>', response)
        results = response['results']
        geographical_data = results[0]['geometry']['location'] # get geographical coordinates
        lat = geographical_data['lat']
        lon = geographical_data['lng']
        return [lat, lon]
    except:
        return [None, None]
    
address = 'Place de la République, Paris, France'
Paris_center = get_coordinates(google_api_key, address)
print('Coordinate of {}: {}'.format(address, Paris_center))

Coordinate of Place de la République, Paris, France: [48.8676635, 2.3640304]


Now let's create a grid of area candidates, equaly spaced, centered around city center and within ~6km from Place de la République. Our neighborhoods will be defined as circular areas with a radius of 300 meters, so our neighborhood centers will be 600 meters apart.

To accurately calculate distances we need to create our grid of locations in Cartesian 2D coordinate system which allows us to calculate distances in meters (not in latitude/longitude degrees). Then we'll project those coordinates back to latitude/longitude degrees to be shown on Folium map. So let's create functions to convert between WGS84 spherical coordinate system (latitude/longitude degrees) and UTM Cartesian coordinate system (X/Y coordinates in  meters).

In [17]:
#!pip install shapely
import shapely

#!pip install pyproj
import pyproj

import math

def lonlat_to_xy(lon, lat):
    proj_latlon = pyproj.Proj(proj='latlong',datum='WGS84')
    proj_xy = pyproj.Proj(proj="utm", zone=33, datum='WGS84')
    xy = pyproj.transform(proj_latlon, proj_xy, lon, lat)
    return xy[0], xy[1]

def xy_to_lonlat(x, y):
    proj_latlon = pyproj.Proj(proj='latlong',datum='WGS84')
    proj_xy = pyproj.Proj(proj="utm", zone=33, datum='WGS84')
    lonlat = pyproj.transform(proj_xy, proj_latlon, x, y)
    return lonlat[0], lonlat[1]

def calc_xy_distance(x1, y1, x2, y2):
    dx = x2 - x1
    dy = y2 - y1
    return math.sqrt(dx*dx + dy*dy)

print('Coordinate transformation check')
print('-------------------------------')
print('Paris center longitude={}, latitude={}'.format(Paris_center[1], Paris_center[0]))
x, y = lonlat_to_xy(Paris_center[1], Paris_center[0])
print('Paris center UTM X={}, Y={}'.format(x, y))
lo, la = xy_to_lonlat(x, y)
print('Paris center longitude={}, latitude={}'.format(lo, la))

Coordinate transformation check
-------------------------------
Paris center longitude=2.3640304, latitude=48.8676635
Paris center UTM X=-425612.40786469076, Y=5490208.939485743
Paris center longitude=2.3640304000000003, latitude=48.8676635


Let's create a **hexagonal grid of cells**: we offset every other row, and adjust vertical row spacing so that **every cell center is equally distant from all it's neighbors**.

In [18]:
Paris_center_x, Paris_center_y = lonlat_to_xy(Paris_center[1], Paris_center[0]) # City center in Cartesian coordinates

k = math.sqrt(3) / 2 # Vertical offset for hexagonal grid cells
x_min = Paris_center_x - 6000
x_step = 600
y_min = Paris_center_y - 6000 - (int(21/k)*k*600 - 12000)/2
y_step = 600 * k 

latitudes = []
longitudes = []
distances_from_center = []
xs = []
ys = []
for i in range(0, int(21/k)):
    y = y_min + i * y_step
    x_offset = 300 if i%2==0 else 0
    for j in range(0, 21):
        x = x_min + j * x_step + x_offset
        distance_from_center = calc_xy_distance(Paris_center_x, Paris_center_y, x, y)
        if (distance_from_center <= 6001):
            lon, lat = xy_to_lonlat(x, y)
            latitudes.append(lat)
            longitudes.append(lon)
            distances_from_center.append(distance_from_center)
            xs.append(x)
            ys.append(y)

print(len(latitudes), 'candidate neighborhood centers generated.')

364 candidate neighborhood centers generated.


Let's visualize the data we have so far: city center location and candidate neighborhood centers:

In [19]:
#!pip install folium

import folium

In [20]:
map_Paris = folium.Map(location=Paris_center, zoom_start=13)
folium.Marker(Paris_center, popup='Place de la République').add_to(map_Paris)
for lat, lon in zip(latitudes, longitudes):
    #folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_Paris) 
    folium.Circle([lat, lon], radius=300, color='blue', fill=False).add_to(map_Paris)
    #folium.Marker([lat, lon]).add_to(map_Paris)
map_Paris

OK, we now have the coordinates of centers of neighborhoods/areas to be evaluated, equally spaced (distance from every point to it's neighbors is exactly the same) and within ~6km from Place de la République. 

Let's now use Google Maps API to get approximate addresses of those locations.

In [21]:

def get_address(api_key, latitude, longitude, verbose=False):
    try:
        url = 'https://maps.googleapis.com/maps/api/geocode/json?key={}&latlng={},{}'.format(api_key, latitude, longitude)
        response = requests.get(url).json()
        if verbose:
            print('Google Maps API JSON result =>', response)
        results = response['results']
        address = results[0]['formatted_address']
        return address
    except:
        return None

addr = get_address(google_api_key, Paris_center[0], Paris_center[1])
print('Reverse geocoding check')
print('-----------------------')
print('Address of [{}, {}] is: {}'.format(Paris_center[0], Paris_center[1], addr))

Reverse geocoding check
-----------------------
Address of [48.8676635, 2.3640304] is: 2 Rue du Faubourg du Temple, 75010 Paris, France


In [22]:
print('Obtaining location addresses: ', end='')
addresses = []
for lat, lon in zip(latitudes, longitudes):
    address = get_address(google_api_key, lat, lon)
    if address is None:
        address = 'NO ADDRESS'
    address = address.replace(', France', '') # We don't need country part of address
    addresses.append(address)
    print(' .', end='')
print(' done.')

Obtaining location addresses:  . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . done.


In [23]:
addresses[150:170]

['93 Rue Charles Delescluze, 93170 Bagnolet',
 '2 Rue des Clos Français, 93100 Montreuil',
 '55 Boulevard Henri Barbusse, 93100 Montreuil',
 '30 Rue Jean Rey, 75015 Paris',
 '12 Avenue Emile Deschanel, 75007 Paris',
 'Invalides la Tour Maubourg, 75007 Paris',
 '136bis Rue de Grenelle, 75007 Paris',
 "51 Rue de l'Université, 75007 Paris",
 'Pont du Carrousel, Pont du Carrousel, 75007 Paris',
 '1 Rue Perrault, 75001 Paris',
 '2 Rue de la Cossonnerie, 75001 Paris',
 '96 Rue du Temple, 75003 Paris',
 '114 Rue de Turenne, 75003 Paris',
 '6 Rue du Marché Popincourt, 75011 Paris',
 '3 Avenue Jean Aicard, 75011 Paris',
 '67 Rue des Amandiers, 75020 Paris',
 '52 Rue Orfila, 75020 Paris',
 '7 Rue de la Dhuis, 75020 Paris',
 '20781 Bd Périphérique, 75020 Paris',
 '64 Rue Malmaison, 93170 Bagnolet']

Looking good. Let's now place all this into a Pandas dataframe.

In [24]:
import pandas as pd

df_locations = pd.DataFrame({'Address': addresses,
                             'Latitude': latitudes,
                             'Longitude': longitudes,
                             'X': xs,
                             'Y': ys,
                             'Distance from center': distances_from_center})

df_locations.head(10)

Address   Latitude  Longitude  \
0               23 Avenue Raspail, 94250 Gentilly  48.814825   2.352930   
1        2 Rue Voltaire, 94270 Le Kremlin-Bicêtre  48.815714   2.360904   
2             46 Rue Barbès, 94200 Ivry-sur-Seine  48.816603   2.368879   
3  16 Sentier de la Liberté, 94200 Ivry-sur-Seine  48.817491   2.376855   
4           1 Rue Paul Mazy, 94200 Ivry-sur-Seine  48.818378   2.384830   
5     27 Rue Jules Vanzuppe, 94200 Ivry-sur-Seine  48.819265   2.392807   
6                  D154B, 94220 Charenton-le-Pont  48.820152   2.400783   
7               9C Boulevard Jourdan, 75014 Paris  48.818051   2.339801   
8                      8 Rue Thomire, 75013 Paris  48.818941   2.347776   
9                      10 Rue Keufer, 75013 Paris  48.819831   2.355751   

               X             Y  Distance from center  
0 -427412.407865  5.484493e+06           5992.495307  
1 -426812.407865  5.484493e+06           5840.376700  
2 -426212.407865  5.484493e+06           5747.173218  
3 -425612.407865  5.484493e+06           5715.767665  
4 -425012.407865  5.484493e+06           5747.173218  
5 -424412.407865  5.484493e+06           5840.376700  
6 -423812.407865  5.484493e+06           5992.495307  
7 -428312.407865  5.485013e+06           5855.766389  
8 -427712.407865  5.485013e+06           5604.462508  
9 -427112.407865  5.485013e+06           5408.326913

...and let's now save/persist this data into local file.

In [25]:
df_locations.to_pickle('./locations.pkl')    

### Foursquare
Now that we have our location candidates, let's use Foursquare API to get info on restaurants in each neighborhood.

We're interested in venues in 'food' category, but only those that are proper restaurants - coffe shops, pizza places, bakeries etc. are not direct competitors so we don't care about those. So we will include in out list only venues that have 'restaurant' in category name, and we'll make sure to detect and include all the subcategories of specific 'Italian restaurant' category, as we need info on Italian restaurants in the neighborhood.

Foursquare credentials are defined in hidden cell bellow.

In [75]:
client_id = 'GetItYourself' # your Foursquare ID
client_secret = 'GetItYourself' # your Foursquare Secret
version = '20200416'
limit = 50
print('Your credentails:')
print('CLIENT_ID: ' + client_id)
print('CLIENT_SECRET:' + client_secret)

Your credentails:
CLIENT_ID: GetItYourself
CLIENT_SECRET:GetItYourself


In [27]:
# Category IDs corresponding to Italian restaurants were taken from Foursquare web site (https://developer.foursquare.com/docs/resources/categories):

food_category = '4d4b7105d754a06374d81259' # 'Root' category for all food-related venues

italian_restaurant_categories = ['4bf58dd8d48988d110941735','55a5a1ebe4b013909087cbb6','55a5a1ebe4b013909087cb7c',
                                 '55a5a1ebe4b013909087cba7','55a5a1ebe4b013909087cba1','55a5a1ebe4b013909087cba4',
                                 '55a5a1ebe4b013909087cb95','55a5a1ebe4b013909087cb89','55a5a1ebe4b013909087cb9b',
                                 '55a5a1ebe4b013909087cb98','55a5a1ebe4b013909087cbbf','55a5a1ebe4b013909087cb79',
                                 '55a5a1ebe4b013909087cbb0','55a5a1ebe4b013909087cbb3','55a5a1ebe4b013909087cb74',
                                 '55a5a1ebe4b013909087cbaa','55a5a1ebe4b013909087cb83','55a5a1ebe4b013909087cb8c',
                                 '55a5a1ebe4b013909087cb92','55a5a1ebe4b013909087cb8f','55a5a1ebe4b013909087cb86',
                                 '55a5a1ebe4b013909087cbb9','55a5a1ebe4b013909087cb7f','55a5a1ebe4b013909087cbbc',
                                 '55a5a1ebe4b013909087cb9e','55a5a1ebe4b013909087cbc2','55a5a1ebe4b013909087cbad']

def is_restaurant(categories, specific_filter=None):
    restaurant_words = ['restaurant', 'diner', 'taverna', 'steakhouse']
    restaurant = False
    specific = False
    for c in categories:
        category_name = c[0].lower()
        category_id = c[1]
        for r in restaurant_words:
            if r in category_name:
                restaurant = True
        if 'fast food' in category_name:
            restaurant = False
        if not(specific_filter is None) and (category_id in specific_filter):
            specific = True
            restaurant = True
    return restaurant, specific

def get_categories(categories):
    return [(cat['name'], cat['id']) for cat in categories]

def format_address(location):
    address = ', '.join(location['formattedAddress'])
    address = address.replace(', France', '')
    return address

def get_venues_near_location(lat, lon, category, client_id, client_secret, radius=500, limit=100):
    version = '20200416'
    url = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&categoryId={}&radius={}&limit={}'.format(
        client_id, client_secret, version, lat, lon, category, radius, limit)
    try:
        results = requests.get(url).json()['response']['groups'][0]['items']
        venues = [(item['venue']['id'],
                   item['venue']['name'],
                   get_categories(item['venue']['categories']),
                   (item['venue']['location']['lat'], item['venue']['location']['lng']),
                   format_address(item['venue']['location']),
                   item['venue']['location']['distance']) for item in results]        
    except:
        venues = []
    return venues

In [29]:
# Let's now go over our neighborhood locations and get nearby restaurants; we'll also maintain a dictionary of all found restaurants and all found italian restaurants

import pickle

def get_restaurants(lats, lons):
    restaurants = {}
    italian_restaurants = {}
    location_restaurants = []

    print('Obtaining venues around candidate locations:', end='')
    for lat, lon in zip(lats, lons):
        # Using radius=350 to meke sure we have overlaps/full coverage so we don't miss any restaurant (we're using dictionaries to remove any duplicates resulting from area overlaps)
        venues = get_venues_near_location(lat, lon, food_category, client_id, client_secret, radius=350, limit=100)
        area_restaurants = []
        for venue in venues:
            venue_id = venue[0]
            venue_name = venue[1]
            venue_categories = venue[2]
            venue_latlon = venue[3]
            venue_address = venue[4]
            venue_distance = venue[5]
            is_res, is_italian = is_restaurant(venue_categories, specific_filter=italian_restaurant_categories)
            if is_res:
                x, y = lonlat_to_xy(venue_latlon[1], venue_latlon[0])
                restaurant = (venue_id, venue_name, venue_latlon[0], venue_latlon[1], venue_address, venue_distance, is_italian, x, y)
                if venue_distance<=300:
                    area_restaurants.append(restaurant)
                restaurants[venue_id] = restaurant
                if is_italian:
                    italian_restaurants[venue_id] = restaurant
        location_restaurants.append(area_restaurants)
        print(' .', end='')
    print(' done.')
    return restaurants, italian_restaurants, location_restaurants

# Try to load from local file system in case we did this before
restaurants = {}
italian_restaurants = {}
location_restaurants = []
loaded = False
try:
    with open('restaurants_350.pkl', 'rb') as f:
        restaurants = pickle.load(f)
    with open('italian_restaurants_350.pkl', 'rb') as f:
        italian_restaurants = pickle.load(f)
    with open('location_restaurants_350.pkl', 'rb') as f:
        location_restaurants = pickle.load(f)
    print('Restaurant data loaded.')
    loaded = True
except:
    pass

# If load failed use the Foursquare API to get the data
if not loaded:
    restaurants, italian_restaurants, location_restaurants = get_restaurants(latitudes, longitudes)
    
    # Let's persists this in local file system
    with open('restaurants_350.pkl', 'wb') as f:
        pickle.dump(restaurants, f)
    with open('italian_restaurants_350.pkl', 'wb') as f:
        pickle.dump(italian_restaurants, f)
    with open('location_restaurants_350.pkl', 'wb') as f:
        pickle.dump(location_restaurants, f)
        

Obtaining venues around candidate locations: . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . . done.


In [30]:
import numpy as np

print('Total number of restaurants:', len(restaurants))
print('Total number of Italian restaurants:', len(italian_restaurants))
print('Percentage of Italian restaurants: {:.2f}%'.format(len(italian_restaurants) / len(restaurants) * 100))
print('Average number of restaurants in neighborhood:', np.array([len(r) for r in location_restaurants]).mean())

Total number of restaurants: 4067
Total number of Italian restaurants: 461
Percentage of Italian restaurants: 11.34%
Average number of restaurants in neighborhood: 9.755494505494505


In [31]:
print('List of all restaurants')
print('-----------------------')
for r in list(restaurants.values())[:10]:
    print(r)
print('...')
print('Total:', len(restaurants))

List of all restaurants
-----------------------
('4e933448d3e30d4e8d0e5c3b', 'Aux Foudres de Bacchus', 48.814739, 2.35158, '20 avenue Raspail, 94250 Gentilly', 99, False, -427512.77155920677, 5484500.312657088)
('4ea93b22775bdf7c3871ddff', 'Quick Ly', 48.814476502609295, 2.350237369537353, '32 avenue Raspail, 94250 Gentilly', 201, False, -427615.9029129003, 5484487.826164405)
('4d381745b274b1f75240e5a3', 'La Terrasse du Marché', 48.815978131305606, 2.350205183029175, '8 place de la Victoire du 8 Mai 1945, 94250 Gentilly', 237, False, -427590.15999008436, 5484654.559065758)
('4ef0802729c22c6c76bb0927', 'La Goulette (spécialités Tunisiennes)', 48.81464536837659, 2.3612059805167442, '2 rue Roger Salengro, 94270 Le Kremlin-Bicètre', 121, False, -426810.3339095134, 5484371.049775164)
('4bc8b3188b7c9c7432b638cf', 'Le Plaza', 48.815603628180504, 2.3605999360912047, '8-10 avenue de Fontainebleau, 94270 Le Kremlin-Bicêtre', 25, True, -426836.75404791755, 5484484.679304826)
('516c6bb7498e19f9f90

In [32]:
print('List of Italian restaurants')
print('---------------------------')
for r in list(italian_restaurants.values())[:10]:
    print(r)
print('...')
print('Total:', len(italian_restaurants))

List of Italian restaurants
---------------------------
('4bc8b3188b7c9c7432b638cf', 'Le Plaza', 48.815603628180504, 2.3605999360912047, '8-10 avenue de Fontainebleau, 94270 Le Kremlin-Bicêtre', 25, True, -426836.75404791755, 5484484.679304826)
('4ba55fa8f964a5207e0039e3', "Fratello's", 48.813508274484995, 2.361317764363373, '37 avenue de Fontainebleau, 94270 Le Kremlin-Bicètre', 247, True, -426823.41338534164, 5484243.713013604)
('4bd02fe8462cb713eddcd707', 'La Toscane', 48.815392993245595, 2.3607132123388386, '9 avenue de Fontainebleau, 94270 Le Kremlin-Bicêtre', 38, True, -426832.40538334555, 5484459.948568966)
('4b7a9763f964a520a5322fe3', 'La Bottina', 48.81860365602536, 2.3744800333370555, '59 Avenue Maurice Thorez, 94200 Ivry-sur-Seine', 213, True, -425765.34195398365, 5484645.718033151)
('4ca4d10eb0ff8cfa3811c35e', "Il Far'niente", 48.82362335218033, 2.330605664073317, '1 rue Paul Fort, 75014 Paris', 306, True, -428880.621370311, 5485743.793684114)
('4cb34a961463a143da7eb3a9', '

In [33]:
print('Restaurants around location')
print('---------------------------')
for i in range(100, 110):
    rs = location_restaurants[i][:8]
    names = ', '.join([r[1] for r in rs])
    print('Restaurants around location {}: {}'.format(i+1, names))

Restaurants around location
---------------------------
Restaurants around location 101: Le Timbre, Les Bistronautes, Moustache, La Table du Luxembourg, Invictus, Gallery
Restaurants around location 102: Le Port Salut, Kokonor, 13 au Jardin, Le Cosi, La Muraille du Phénix, Restaurant Perraudin, Fuxia, Terra Nova
Restaurants around location 103: Nossa Churrasqueira, Godjo, Ciasa Mia, Le Coupe-Chou, LeFoodist, Le Petit Prince de Paris, I Lazzari, Lhassa
Restaurants around location 104: Au Moulin à Vent, La Tour d'Argent, Restaurant AT, Le Buisson Ardent, Chez René, La Rôtisserie, L'Atlas, La Rose de Damas
Restaurants around location 105: Gentle Gourmet Café
Restaurants around location 106: Dersou, Passerini, Assaporare, À la Biche au Bois, L'Encrier, Miss Lunch, Chez Papa, Quatre Amis
Restaurants around location 107: L'Ébauchoir, Will, East Mamma, Le Goyavier, L'Ami Pierre, Menekse, Do & Riz, Virtus
Restaurants around location 108: Au Petit Panisse, Fulgurances l'Adresse, Midam, Chez Ant

Let's now see all the collected restaurants in our area of interest on map, and let's also show Italian restaurants in different color.

In [34]:
map_Paris = folium.Map(location=Paris_center, zoom_start=13)
folium.Marker(Paris_center, popup='Place de la République').add_to(map_Paris)
for res in restaurants.values():
    lat = res[2]; lon = res[3]
    is_italian = res[6]
    color = 'red' if is_italian else 'blue'
    folium.CircleMarker([lat, lon], radius=3, color=color, fill=True, fill_color=color, fill_opacity=1).add_to(map_Paris)
map_Paris

Looking good. So now we have all the restaurants in area within few kilometers from Place de la République, and we know which ones are Italian restaurants! We also know which restaurants exactly are in vicinity of every neighborhood candidate center.

This concludes the data gathering phase - we're now ready to use this data for analysis to produce the report on optimal locations for a new Italian restaurant!

## Methodology <a name="methodology"></a>

In this project we will direct our efforts on detecting areas of Paris that have low restaurant density, particularly those with low number of Italian restaurants. We will limit our analysis to area ~6km around city center.

In first step we have collected the required **data: location and type (category) of every restaurant within 6km from Paris center** (Place de la République). We have also **identified Italian restaurants** (according to Foursquare categorization).

Second step in our analysis will be calculation and exploration of '**restaurant density**' across different areas of Paris - we will use **heatmaps** to identify a few promising areas close to center with low number of restaurants in general (*and* no Italian restaurants in vicinity) and focus our attention on those areas.

In third and final step we will focus on most promising areas and within those create **clusters of locations that meet some basic requirements** established in discussion with stakeholders: we will take into consideration locations with **no more than two restaurants in radius of 250 meters**, and we want locations **without Italian restaurants in radius of 400 meters**. We will present map of all such locations but also create clusters (using **k-means clustering**) of those locations to identify general zones / neighborhoods / addresses which should be a starting point for final 'street level' exploration and search for optimal venue location by stakeholders.

## Analysis <a name="analysis"></a>

Let's perform some basic explanatory data analysis and derive some additional info from our raw data. First let's count the **number of restaurants in every area candidate**:

In [35]:
location_restaurants_count = [len(res) for res in location_restaurants]

df_locations['Restaurants in area'] = location_restaurants_count

print('Average number of restaurants in every area with radius=300m:', np.array(location_restaurants_count).mean())

df_locations.head(10)

Average number of restaurants in every area with radius=300m: 9.755494505494505


Address   Latitude  Longitude  \
0               23 Avenue Raspail, 94250 Gentilly  48.814825   2.352930   
1        2 Rue Voltaire, 94270 Le Kremlin-Bicêtre  48.815714   2.360904   
2             46 Rue Barbès, 94200 Ivry-sur-Seine  48.816603   2.368879   
3  16 Sentier de la Liberté, 94200 Ivry-sur-Seine  48.817491   2.376855   
4           1 Rue Paul Mazy, 94200 Ivry-sur-Seine  48.818378   2.384830   
5     27 Rue Jules Vanzuppe, 94200 Ivry-sur-Seine  48.819265   2.392807   
6                  D154B, 94220 Charenton-le-Pont  48.820152   2.400783   
7               9C Boulevard Jourdan, 75014 Paris  48.818051   2.339801   
8                      8 Rue Thomire, 75013 Paris  48.818941   2.347776   
9                      10 Rue Keufer, 75013 Paris  48.819831   2.355751   

               X             Y  Distance from center  Restaurants in area  
0 -427412.407865  5.484493e+06           5992.495307                    3  
1 -426812.407865  5.484493e+06           5840.376700                    7  
2 -426212.407865  5.484493e+06           5747.173218                    3  
3 -425612.407865  5.484493e+06           5715.767665                    6  
4 -425012.407865  5.484493e+06           5747.173218                    0  
5 -424412.407865  5.484493e+06           5840.376700                    3  
6 -423812.407865  5.484493e+06           5992.495307                    1  
7 -428312.407865  5.485013e+06           5855.766389                    3  
8 -427712.407865  5.485013e+06           5604.462508                    0  
9 -427112.407865  5.485013e+06           5408.326913                    1

OK, now let's calculate the **distance to nearest Italian restaurant from every area candidate center** (not only those within 300m - we want distance to closest one, regardless of how distant it is).

In [36]:
distances_to_italian_restaurant = []

for area_x, area_y in zip(xs, ys):
    min_distance = 10000
    for res in italian_restaurants.values():
        res_x = res[7]
        res_y = res[8]
        d = calc_xy_distance(area_x, area_y, res_x, res_y)
        if d<min_distance:
            min_distance = d
    distances_to_italian_restaurant.append(min_distance)

df_locations['Distance to Italian restaurant'] = distances_to_italian_restaurant

In [37]:
df_locations.head(10)

Address   Latitude  Longitude  \
0               23 Avenue Raspail, 94250 Gentilly  48.814825   2.352930   
1        2 Rue Voltaire, 94270 Le Kremlin-Bicêtre  48.815714   2.360904   
2             46 Rue Barbès, 94200 Ivry-sur-Seine  48.816603   2.368879   
3  16 Sentier de la Liberté, 94200 Ivry-sur-Seine  48.817491   2.376855   
4           1 Rue Paul Mazy, 94200 Ivry-sur-Seine  48.818378   2.384830   
5     27 Rue Jules Vanzuppe, 94200 Ivry-sur-Seine  48.819265   2.392807   
6                  D154B, 94220 Charenton-le-Pont  48.820152   2.400783   
7               9C Boulevard Jourdan, 75014 Paris  48.818051   2.339801   
8                      8 Rue Thomire, 75013 Paris  48.818941   2.347776   
9                      10 Rue Keufer, 75013 Paris  48.819831   2.355751   

               X             Y  Distance from center  Restaurants in area  \
0 -427412.407865  5.484493e+06           5992.495307                    3   
1 -426812.407865  5.484493e+06           5840.376700                    7   
2 -426212.407865  5.484493e+06           5747.173218                    3   
3 -425612.407865  5.484493e+06           5715.767665                    6   
4 -425012.407865  5.484493e+06           5747.173218                    0   
5 -424412.407865  5.484493e+06           5840.376700                    3   
6 -423812.407865  5.484493e+06           5992.495307                    1   
7 -428312.407865  5.485013e+06           5855.766389                    3   
8 -427712.407865  5.485013e+06           5604.462508                    0   
9 -427112.407865  5.485013e+06           5408.326913                    1   

   Distance to Italian restaurant  
0                      575.716458  
1                       25.784869  
2                      472.375143  
3                      216.007367  
4                      768.231794  
5                     1361.506885  
6                     1782.291034  
7                      415.518488  
8                      444.507198  
9                      595.720430

In [38]:
print('Average distance to closest Italian restaurant from each area center:', df_locations['Distance to Italian restaurant'].mean())

Average distance to closest Italian restaurant from each area center: 420.93064385158203


OK, so **on average Italian restaurant can be found within ~420m** from every area center candidate. That's fairly close, so we need to filter our areas carefully!

Let's crete a map showing **heatmap / density of restaurants** and try to extract some meaningfull info from that. Also, let's show **borders of Paris boroughs** on our map and a few circles indicating distance of 1km, 2km and 3km from Place de la République.

In [39]:
Paris_boroughs_url = 'https://opendata.paris.fr/explore/dataset/arrondissements/download/?format=geojson&timezone=Europe/Berlin&lang=fr'
Paris_boroughs = requests.get(Paris_boroughs_url).json()

def boroughs_style(feature):
    return { 'color': 'blue', 'fill': False }

In [41]:
restaurant_latlons = [[res[2], res[3]] for res in restaurants.values()]

italian_latlons = [[res[2], res[3]] for res in italian_restaurants.values()]

In [42]:
from folium import plugins
from folium.plugins import HeatMap

map_Paris = folium.Map(location=Paris_center, zoom_start=13)
folium.TileLayer('cartodbpositron').add_to(map_Paris) #cartodbpositron cartodbdark_matter
HeatMap(restaurant_latlons).add_to(map_Paris)
folium.Marker(Paris_center).add_to(map_Paris)
folium.Circle(Paris_center, radius=1000, fill=False, color='white').add_to(map_Paris)
folium.Circle(Paris_center, radius=2000, fill=False, color='white').add_to(map_Paris)
folium.Circle(Paris_center, radius=3000, fill=False, color='white').add_to(map_Paris)
folium.GeoJson(Paris_boroughs, style_function=boroughs_style, name='geojson').add_to(map_Paris)
map_Paris

Looks like a few pockets of low restaurant density closest to city center can be found **south, south-east and east from Place de la République**. 

Let's create another heatmap map showing **heatmap/density of Italian restaurants** only.

In [43]:
map_Paris = folium.Map(location=Paris_center, zoom_start=13)
folium.TileLayer('cartodbpositron').add_to(map_Paris) #cartodbpositron cartodbdark_matter
HeatMap(italian_latlons).add_to(map_Paris)
folium.Marker(Paris_center).add_to(map_Paris)
folium.Circle(Paris_center, radius=1000, fill=False, color='white').add_to(map_Paris)
folium.Circle(Paris_center, radius=2000, fill=False, color='white').add_to(map_Paris)
folium.Circle(Paris_center, radius=3000, fill=False, color='white').add_to(map_Paris)
folium.GeoJson(Paris_boroughs, style_function=boroughs_style, name='geojson').add_to(map_Paris)
map_Paris

This map indicates higher density of existing Italian restaurants directly north and west from Place de la République, with closest pockets of **low Italian restaurant density positioned east, south-east and south from city center**.

Based on this we will now focus our analysis on areas *south-west, south, south-east and east from Paris center* - we will move the center of our area of interest and reduce it's size to have a radius of **2.5km**. This places our location candidates mostly in boroughs **Le Marais** or **Quartier Picpus**

### Le Marais & Picpus

As a French guy I used to visit thoses places. These neighbordhoods are very well deserved and with good animation in the street. It would be a good place.

In [44]:
roi_x_min = Paris_center_x - 2000
roi_y_max = Paris_center_y + 1000
roi_width = 5000
roi_height = 5000
roi_center_x = roi_x_min + 2500
roi_center_y = roi_y_max - 2500
roi_center_lon, roi_center_lat = xy_to_lonlat(roi_center_x, roi_center_y)
roi_center = [roi_center_lat, roi_center_lon]

map_Paris = folium.Map(location=roi_center, zoom_start=14)
HeatMap(restaurant_latlons).add_to(map_Paris)
folium.Marker(Paris_center).add_to(map_Paris)
folium.Circle(roi_center, radius=2500, color='white', fill=True, fill_opacity=0.4).add_to(map_Paris)
folium.GeoJson(Paris_boroughs, style_function=boroughs_style, name='geojson').add_to(map_Paris)
map_Paris

In [45]:
k = math.sqrt(3) / 2 # Vertical offset for hexagonal grid cells
x_step = 100
y_step = 100 * k 
roi_y_min = roi_center_y - 2500

roi_latitudes = []
roi_longitudes = []
roi_xs = []
roi_ys = []
for i in range(0, int(51/k)):
    y = roi_y_min + i * y_step
    x_offset = 50 if i%2==0 else 0
    for j in range(0, 51):
        x = roi_x_min + j * x_step + x_offset
        d = calc_xy_distance(roi_center_x, roi_center_y, x, y)
        if (d <= 2501):
            lon, lat = xy_to_lonlat(x, y)
            roi_latitudes.append(lat)
            roi_longitudes.append(lon)
            roi_xs.append(x)
            roi_ys.append(y)

print(len(roi_latitudes), 'candidate neighborhood centers generated.')

2261 candidate neighborhood centers generated.


OK. Now let's calculate two most important things for each location candidate: **number of restaurants in vicinity** (we'll use radius of **250 meters**) and **distance to closest Italian restaurant**.

In [46]:
def count_restaurants_nearby(x, y, restaurants, radius=250):    
    count = 0
    for res in restaurants.values():
        res_x = res[7]; res_y = res[8]
        d = calc_xy_distance(x, y, res_x, res_y)
        if d<=radius:
            count += 1
    return count

def find_nearest_restaurant(x, y, restaurants):
    d_min = 100000
    for res in restaurants.values():
        res_x = res[7]; res_y = res[8]
        d = calc_xy_distance(x, y, res_x, res_y)
        if d<=d_min:
            d_min = d
    return d_min

roi_restaurant_counts = []
roi_italian_distances = []

print('Generating data on location candidates... ', end='')
for x, y in zip(roi_xs, roi_ys):
    count = count_restaurants_nearby(x, y, restaurants, radius=250)
    roi_restaurant_counts.append(count)
    distance = find_nearest_restaurant(x, y, italian_restaurants)
    roi_italian_distances.append(distance)
print('done.')


Generating data on location candidates... done.


In [47]:
# Let's put this into dataframe
df_roi_locations = pd.DataFrame({'Latitude':roi_latitudes,
                                 'Longitude':roi_longitudes,
                                 'X':roi_xs,
                                 'Y':roi_ys,
                                 'Restaurants nearby':roi_restaurant_counts,
                                 'Distance to Italian restaurant':roi_italian_distances})

df_roi_locations.head(10)

Latitude  Longitude              X             Y  Restaurants nearby  \
0  48.833218   2.378992 -425162.407865  5.486209e+06                   2   
1  48.833366   2.380322 -425062.407865  5.486209e+06                   2   
2  48.833164   2.371485 -425712.407865  5.486296e+06                   6   
3  48.833312   2.372815 -425612.407865  5.486296e+06                   6   
4  48.833460   2.374144 -425512.407865  5.486296e+06                   3   
5  48.833608   2.375474 -425412.407865  5.486296e+06                   3   
6  48.833756   2.376804 -425312.407865  5.486296e+06                   4   
7  48.833904   2.378133 -425212.407865  5.486296e+06                   2   
8  48.834052   2.379463 -425112.407865  5.486296e+06                   2   
9  48.834200   2.380793 -425012.407865  5.486296e+06                   0   

   Distance to Italian restaurant  
0                      317.037739  
1                      397.993054  
2                      131.962373  
3                      116.236013  
4                      170.345308  
5                      254.016214  
6                      307.700049  
7                      350.092650  
8                      412.856399  
9                      375.563755

OK. Let us now **filter** those locations: we're interested only in **locations with no more than two restaurants in radius of 250 meters**, and **no Italian restaurants in radius of 400 meters**.

In [48]:
good_res_count = np.array((df_roi_locations['Restaurants nearby']<=2))
print('Locations with no more than two restaurants nearby:', good_res_count.sum())

good_ita_distance = np.array(df_roi_locations['Distance to Italian restaurant']>=400)
print('Locations with no Italian restaurants within 400m:', good_ita_distance.sum())

good_locations = np.logical_and(good_res_count, good_ita_distance)
print('Locations with both conditions met:', good_locations.sum())

df_good_locations = df_roi_locations[good_locations]


Locations with no more than two restaurants nearby: 248
Locations with no Italian restaurants within 400m: 372
Locations with both conditions met: 123


Let's see how this looks on a map.

In [49]:
good_latitudes = df_good_locations['Latitude'].values
good_longitudes = df_good_locations['Longitude'].values

good_locations = [[lat, lon] for lat, lon in zip(good_latitudes, good_longitudes)]

map_Paris = folium.Map(location=roi_center, zoom_start=14)
folium.TileLayer('cartodbpositron').add_to(map_Paris)
HeatMap(restaurant_latlons).add_to(map_Paris)
folium.Circle(roi_center, radius=2500, color='white', fill=True, fill_opacity=0.6).add_to(map_Paris)
folium.Marker(Paris_center).add_to(map_Paris)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_Paris) 
folium.GeoJson(Paris_boroughs, style_function=boroughs_style, name='geojson').add_to(map_Paris)
map_Paris

Looking good. We now have a bunch of locations fairly close to Place de la République, and we know that each of those locations has no more than two restaurants in radius of 250m, and no Italian restaurant closer than 400m. Any of those locations is a potential candidate for a new Italian restaurant, at least based on nearby competition.

Let's now show those good locations in a form of heatmap:

In [50]:
map_Paris = folium.Map(location=roi_center, zoom_start=14)
HeatMap(good_locations, radius=25).add_to(map_Paris)
folium.Marker(Paris_center).add_to(map_Paris)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_Paris)
folium.GeoJson(Paris_boroughs, style_function=boroughs_style, name='geojson').add_to(map_Paris)
map_Paris

Looking good. What we have now is a clear indication of zones with low number of restaurants in vicinity, and *no* Italian restaurants at all nearby.

It's interesting to see that a zone of "Cimetière du Père Lachaize" is identified as good place... For sur it is a famous graveyard in Paris ! 

Let us now **cluster** those locations to create **centers of zones containing good locations**. Those zones, their centers and addresses will be the final result of our analysis. 

In [51]:
from sklearn.cluster import KMeans

number_of_clusters = 15

good_xys = df_good_locations[['X', 'Y']].values
kmeans = KMeans(n_clusters=number_of_clusters, random_state=0).fit(good_xys)

cluster_centers = [xy_to_lonlat(cc[0], cc[1]) for cc in kmeans.cluster_centers_]

map_Paris = folium.Map(location=roi_center, zoom_start=14)
folium.TileLayer('cartodbpositron').add_to(map_Paris)
HeatMap(restaurant_latlons).add_to(map_Paris)
folium.Circle(roi_center, radius=2500, color='white', fill=True, fill_opacity=0.4).add_to(map_Paris)
folium.Marker(Paris_center).add_to(map_Paris)
for lon, lat in cluster_centers:
    folium.Circle([lat, lon], radius=500, color='green', fill=True, fill_opacity=0.25).add_to(map_Paris) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_Paris)
folium.GeoJson(Paris_boroughs, style_function=boroughs_style, name='geojson').add_to(map_Paris)
map_Paris

Not bad - our clusters represent groupings of most of the candidate locations and cluster centers are placed nicely in the middle of the zones 'rich' with location candidates.

Addresses of those cluster centers will be a good starting point for exploring the neighborhoods to find the best possible location based on neighborhood specifics.

Let's see those zones on a city map without heatmap, using shaded areas to indicate our clusters:

In [52]:
map_Paris = folium.Map(location=roi_center, zoom_start=14)
folium.Marker(Paris_center).add_to(map_Paris)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.Circle([lat, lon], radius=250, color='#00000000', fill=True, fill_color='#0066ff', fill_opacity=0.07).add_to(map_Paris)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_Paris)
for lon, lat in cluster_centers:
    folium.Circle([lat, lon], radius=500, color='green', fill=False).add_to(map_Paris) 
folium.GeoJson(Paris_boroughs, style_function=boroughs_style, name='geojson').add_to(map_Paris)
map_Paris

Let's zoom in on candidate areas in **Picpus**:

In [74]:
map_Paris = folium.Map(location=[48.8498976, 2.364446], zoom_start=16)
folium.Marker(Paris_center).add_to(map_Paris)
for lon, lat in cluster_centers:
    folium.Circle([lat, lon], radius=500, color='green', fill=False).add_to(map_Paris) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.Circle([lat, lon], radius=250, color='#0000ff00', fill=True, fill_color='#0066ff', fill_opacity=0.07).add_to(map_Paris)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_Paris)
folium.GeoJson(Paris_boroughs, style_function=boroughs_style, name='geojson').add_to(map_Paris)
map_Paris

...and candidate areas in **Picpus**:

In [65]:
map_Paris = folium.Map(location=[48.8461795, 2.3948071], zoom_start=15)
folium.Marker(Paris_center).add_to(map_Paris)
for lon, lat in cluster_centers:
    folium.Circle([lat, lon], radius=500, color='green', fill=False).add_to(map_Paris) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.Circle([lat, lon], radius=250, color='#0000ff00', fill=True, fill_color='#0066ff', fill_opacity=0.07).add_to(map_Paris)
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.CircleMarker([lat, lon], radius=2, color='blue', fill=True, fill_color='blue', fill_opacity=1).add_to(map_Paris)
folium.GeoJson(Paris_boroughs, style_function=boroughs_style, name='geojson').add_to(map_Paris)
map_Paris

Finaly, let's **reverse geocode those candidate area centers to get the addresses** which can be presented to stakeholders.

In [68]:
candidate_area_addresses = []
print('==============================================================')
print('Addresses of centers of areas recommended for further analysis')
print('==============================================================\n')
for lon, lat in cluster_centers:
    addr = get_address(google_api_key, lat, lon).replace(', France', '')
    candidate_area_addresses.append(addr)    
    x, y = lonlat_to_xy(lon, lat)
    d = calc_xy_distance(x, y, Paris_center_x, Paris_center_y)
    print('{}{} => {:.1f}km from Place de la République'.format(addr, ' '*(50-len(addr)), d/1000))
    

Addresses of centers of areas recommended for further analysis

Pont d'Austerlitz, Pont d'Austerlitz, 75012 Paris  => 2.5km from Place de la République
7 Rue du Clos, 75020 Paris                         => 3.3km from Place de la République
40 Rue de Picpus, 75012 Paris                      => 3.4km from Place de la République
16 Rue des Rigoles, 75020 Paris                    => 2.3km from Place de la République
Cimetière Père Lachaise, 16 rue du repos, 71ème division, Avenue Circulaire, 75020 Paris => 2.1km from Place de la République
11 Port de la Gare, 75013 Paris                    => 3.9km from Place de la République
Division Pinel, 75013 Paris                        => 3.4km from Place de la République
11 Bis Quai Saint-Bernard, 75005 Paris             => 2.2km from Place de la République
66 Quai d'Austerlitz, 75013 Paris                  => 2.9km from Place de la République
Cimetière Père Lachaise, 16 rue du repos, 43ème division, Avenue Transversale n°1, 75020 Paris => 2.5km fr

This concludes our analysis. We have created 15 addresses representing centers of zones containing locations with low number of restaurants and no Italian restaurants nearby, all zones being fairly close to city center (all less than 4km from Place de la République, and about half of those less than 2km from Place de la République). Although zones are shown on map with a radius of ~500 meters (green circles), their shape is actually very irregular and their centers/addresses should be considered only as a starting point for exploring area neighborhoods in search for potential restaurant locations. Most of the zones are located in Picpus and Le Marais boroughs, which we have identified as interesting due to being popular with tourists, fairly close to city center and well connected by public transport.

In [69]:
map_Paris = folium.Map(location=roi_center, zoom_start=14)
folium.Circle(Paris_center, radius=50, color='red', fill=True, fill_color='red', fill_opacity=1).add_to(map_Paris)
for lonlat, addr in zip(cluster_centers, candidate_area_addresses):
    folium.Marker([lonlat[1], lonlat[0]], popup=addr).add_to(map_Paris) 
for lat, lon in zip(good_latitudes, good_longitudes):
    folium.Circle([lat, lon], radius=250, color='#0000ff00', fill=True, fill_color='#0066ff', fill_opacity=0.05).add_to(map_Paris)
map_Paris

## Results and Discussion <a name="results"></a>

Our analysis shows that although there is a great number of restaurants in Paris (~2000 in our initial area of interest which was 12x12km around Place de la République), there are pockets of low restaurant density fairly close to city center. We focused our attention to areas south, south-east and east, corresponding to boroughs Picpus and Le Marais. Our attention was focused on Picpus and Le Marais which offer a combination of popularity among tourists, closeness to city center, strong socio-economic dynamics *and* a number of pockets of low restaurant density.

After directing our attention to this more narrow area of interest (covering approx. 5x5km south-east from Place de la République) we first created a dense grid of location candidates (spaced 100m appart); those locations were then filtered so that those with more than two restaurants in radius of 250m and those with an Italian restaurant closer than 400m were removed.

Those location candidates were then clustered to create zones of interest which contain greatest number of location candidates. Addresses of centers of those zones were also generated using reverse geocoding to be used as markers/starting points for more detailed local analysis based on other factors.

Result of all this is 15 zones containing largest number of potential new restaurant locations based on number of and distance to existing venues - both restaurants in general and Italian restaurants particularly. This, of course, does not imply that those zones are actually optimal locations for a new restaurant! Purpose of this analysis was to only provide info on areas close to Paris center but not crowded with existing restaurants (particularly Italian) - it is entirely possible that there is a very good reason for small number of restaurants in any of those areas, reasons which would make them unsuitable for a new restaurant regardless of lack of competition in the area. Recommended zones should therefore be considered only as a starting point for more detailed analysis which could eventually result in location which has not only no nearby competition but also other factors taken into account and all other relevant conditions met.

## Conclusion <a name="conclusion"></a>

Purpose of this project was to identify Paris areas close to center with low number of restaurants (particularly Italian restaurants) in order to aid stakeholders in narrowing down the search for optimal location for a new Italian restaurant. By calculating restaurant density distribution from Foursquare data we have first identified general boroughs that justify further analysis (Picpus and Le Marais), and then generated extensive collection of locations which satisfy some basic requirements regarding existing nearby restaurants. Clustering of those locations was then performed in order to create major zones of interest (containing greatest number of potential locations) and addresses of those zone centers were created to be used as starting points for final exploration by stakeholders.

Final decission on optimal restaurant location will be made by stakeholders based on specific characteristics of neighborhoods and locations in every recommended zone, taking into consideration additional factors like attractiveness of each location (proximity to park or water), levels of noise / proximity to major roads, real estate availability, prices, social and economic dynamics of every neighborhood etc.